# Boundary Pass and ONC Central Node Results Time Series

Assemble time series results for Rich:

* NEMO-3.6 nowcast-green runs
* full water column
* hourly average results at Boundary Pass location of ONC mooring
* hourly average results at ONC central node
* 1-Jun-2016 through 30-Sep-2016

After the planned NEMO-3.6 hindcast runs it should be possible to increase the time resolution
to 10 minute averages.

In [1]:
import os
from pathlib import Path

import arrow
import xarray

In [2]:
# ONC description of central node location:
# Depth: 297 m
# Latitude: 49.040066666
# Longitude: -123.425825
central_ji = (424, 266)
# ONC description of Boundary Pass mooring location:
# Depth: 230 m
# Latitude: 48.7665
# Longitude: -123.039556
boundary_ji = (343, 289)

start_date = arrow.get('2016-06-01')
end_date = arrow.get('2016-06-02')

results_archive = Path('/results/SalishSea/nowcast-green/')

In [3]:
def write_csv(filehandle, time_counter, var):
    for i, t in enumerate(time_counter.values):
        mat_timestamp = arrow.get((str(t))).format('D-MMM-YYYY HH:mm:ss Z')
        line = ', '.join(str(v) for v in var.values[i])
        line = ', '.join((mat_timestamp, line))
        line = f'{line}\n'
        f.write(line)
        print(mat_timestamp)

In [4]:
datasets = []
for a in arrow.Arrow.range('day', start_date, end_date):
    ddmmmyy = a.format('DDMMMYY').lower()
    yyyymmdd = a.format('YYYYMMDD')
    results_dir = f'{ddmmmyy}'
    grid_T_1h = f'SalishSea_1h_{yyyymmdd}_{yyyymmdd}_grid_T.nc'
    datasets.append(os.fspath(results_archive/results_dir/grid_T_1h))

In [5]:
datasets

['/results/SalishSea/nowcast-green/01jun16/SalishSea_1h_20160601_20160601_grid_T.nc',
 '/results/SalishSea/nowcast-green/02jun16/SalishSea_1h_20160602_20160602_grid_T.nc']

In [6]:
%%time

var = 'vosaline'
locn = central_ji
filepath = Path('central_salinity.csv')

with filepath.open('wt') as f:
    for dataset in datasets:
        with xarray.open_dataset(dataset) as ds:
            ds_var = ds.data_vars[var].isel(y=locn[0], x=locn[1])
            write_csv(f, ds.time_counter, ds_var)

1-Jun-2016 00:30:00 +0000
1-Jun-2016 01:30:00 +0000
1-Jun-2016 02:30:00 +0000
1-Jun-2016 03:30:00 +0000
1-Jun-2016 04:30:00 +0000
1-Jun-2016 05:30:00 +0000
1-Jun-2016 06:30:00 +0000
1-Jun-2016 07:30:00 +0000
1-Jun-2016 08:30:00 +0000
1-Jun-2016 09:30:00 +0000
1-Jun-2016 10:30:00 +0000
1-Jun-2016 11:30:00 +0000
1-Jun-2016 12:30:00 +0000
1-Jun-2016 13:30:00 +0000
1-Jun-2016 14:30:00 +0000
1-Jun-2016 15:30:00 +0000
1-Jun-2016 16:30:00 +0000
1-Jun-2016 17:30:00 +0000
1-Jun-2016 18:30:00 +0000
1-Jun-2016 19:30:00 +0000
1-Jun-2016 20:30:00 +0000
1-Jun-2016 21:30:00 +0000
1-Jun-2016 22:30:00 +0000
1-Jun-2016 23:30:00 +0000
2-Jun-2016 00:30:00 +0000
2-Jun-2016 01:30:00 +0000
2-Jun-2016 02:30:00 +0000
2-Jun-2016 03:30:00 +0000
2-Jun-2016 04:30:00 +0000
2-Jun-2016 05:30:00 +0000
2-Jun-2016 06:30:00 +0000
2-Jun-2016 07:30:00 +0000
2-Jun-2016 08:30:00 +0000
2-Jun-2016 09:30:00 +0000
2-Jun-2016 10:30:00 +0000
2-Jun-2016 11:30:00 +0000
2-Jun-2016 12:30:00 +0000
2-Jun-2016 13:30:00 +0000
2-Jun-2016 1

Best observed timings:

In notebook:

Using xarray.open_mf_dataset() for 1 day's results:

    CPU times: user 1min 41s, sys: 3min 53s, total: 5min 35s
    Wall time: 5min 35s

Using xarray.open_dataset() for 1 day's results:

    CPU times: user 3.82 s, sys: 756 ms, total: 4.58 s
    Wall time: 4.82 s
    
From command-line:

Using xarray.open_mf_dataset() for 1 day's results:


Using xarray.open_dataset() for 1 day's results:

    real	0m11.714s
    user	0m8.140s
    sys	0m2.644s

## Depths

In [12]:
with Path('depths.csv').open('wt') as f:
     with xarray.open_dataset(datasets[0]) as ds:
        for depth in ds.deptht.values:
            f.write(f'{depth}\n')